In [484]:
from urllib import request
from PIL import Image
import PIL.ImageOps  
import time

In [485]:
import requests

In [486]:
import re

In [487]:
from bs4 import BeautifulSoup as bs

In [488]:
from openpyxl import Workbook

In [489]:
from openpyxl import load_workbook

In [490]:
import os

In [491]:
from skimage.io import imread

In [492]:
import re

In [493]:
datasetpath="/Users/soulist/Projects/dataset.xlsx"
imagedatasetpath="Users/soulist/Projects/imagedataset" 
wb=load_workbook("/Users/soulist/Projects/dataset.xlsx")
ws=wb.active
url="https://artinvestment.ru/auctions/"
row=1


In [494]:

lastpage=482
def search (url=url):
    artistid=0
    paintingid=0
    page=1
    rmain=requests.get(url)
#                        +str(page))
#                        +"&citems=5")
    soupmain=bs(rmain.text)

    while page<=lastpage:
        artistlist=soupmain.findAll("div",{"class":"artists-list"})
        painterlinks=[]
# Listing through the artists on the page (Проходимся по всем художникам на странице)
        for i in artistlist:   
            artistid+=1
            print(artistid)
            print(i.a.text,i.a["href"])
            artistname=i.a.text
            print(paintings(i.a["href"]+"/works.html",artistid,artistname)) 
#         Switching the page when no artists left
        page+=1
        rmain=requests.get("https://artinvestment.ru/auctions/?page="+str(page))
#                            +"&citems=5")
        soupmain=bs(rmain.text)   
        print("Страница - "+page)
    return ("Следующий")
def paintings (link,artistid,artistname):
        start = time.clock()
        listitem="list-item"
        page=1
        paintingid=0
        paintingartisauctiontid=0
        
        r=requests.get(link)
        soup=bs(r.text)
        print(link)
#   Looking for class "list-item" on the page. If present, then some painting is present.
# Ищем класс "list-item" на страничке. Если он присутствует, то какая-либо картина также присутствует.
        while listitem in r.text:

            global row
#             Looking for the painting's title (Ищем название картины)
            try:
                listitems=soup.find("div",{"class":"list-items"})
            except AttributeError:
                return
            try:
                paintingslist=listitems.findAll("div",{"class":"list-item"})
            except AttributeError:
                return
            for i in paintingslist:  
                    auctionid=1
                    column=7
                    paintingid+=1
                    print(paintingid)
                    paintingartisauctiontid=str(artistid)+str(paintingid)+str(auctionid)
                    ws["A"+str(row)]=paintingartisauctiontid
                    ws["B"+str(row)]=artistname
                    
                    if i.h3.text=="Перейти к работе":
                        print ("Безымянная")
                        ws["C"+str(row)]="Безымянная"
                    else:
                        print (i.h3.text)
                        ws["C"+str(row)]=i.h3.text
                    
                    print("Следующая картина")
#             Assigning year,size and technique characteristics to variables (Назначаем переменные с данными о годе создания, размере и технике)
                    year=re.findall(r"\d{4}",i.text)
                    size=re.findall(r".+\d+х\d+.+",i.text)
                    technique=re.findall(r".+;.+",i.text)

#             Printing out and writing the characteristics in excel (Распечатываем характеристики и записываем их в Эксель)
                    if len(size)!=0:
                        sizestr="".join(size)
                        print ("Размер -",sizestr)
                        sizestr.replace("Размер, ","")
                        ws["E"+str(row)]="".join(size)
                    if len(technique)!=0:
                        print ("Техника -","".join(technique))
                        ws["F"+str(row)]="".join(technique)
                    header=i.find("div",{"class":"header"})
                    print(paintingartisauctiontid)
# Finding the year of creation (Находим год создания и записываем в Excel)
                    values=i.findAll("div",{"class":"value"})
                    for v in values:
                        try:
                            year="".join(re.findall(r"^\d{4}",v.get_text()))
                            if len(year)>0:
                                print (year)
                                ws["D"+str(row)]="".join(year)
                        except AttributeError:
                            continue
#             Risk Labeling (Ищем маркировку риска и записываем в Excel)
                    labelyellow=i.find("span",{"class":"yellow round"})
                    labelgreen=i.find("span",{"class":"green round"})
                    labelred=i.find("span",{"class":"red round"})
                    label=[]
                    if labelyellow is not None:
                        label=[]
                        label.append(labelyellow["class"])
                    if labelgreen is not None:
                        label=[]
                        label.append(labelgreen["class"])
                    if labelred is not None: 
                        label=[]
                        label.append(labelred["class"])
                    try:

                        ws["L"+str(row)]=("".join(label[0]))
                    except IndexError:
                        ws["L"+str(row)]="No Label"

    #                 Downloading an image (Скачиваем изображение)
                    linktoimage=i.find("img")
                    imagepath=("/Users/soulist/Projects/imagedataset/"+str(paintingartisauctiontid)+".jpg")
                    try:
                        imageurl=linktoimage["src"].replace("small","big")    
                        request.urlretrieve(imageurl,imagepath)
                        ws["M"+str(row)]=imageurl
                    except KeyboardInterrupt:
                        raise
                    except:
                        continue
    #         Inverting the negative (Инвертируем цвета)
    #                 image = Image.open(imagepath)
    #                 inverted_image = PIL.ImageOps.invert(image)
    #                 inverted_image.save(imagepath)
    
    
# Collecting the data about last auction (Собираем данные о последнем аукционе)
                    for elm in header.find_next_sibling("div").find_all("div"):
                        print(elm.getText())
                        ws.cell(row=row,column=column).value=elm.get_text()
                        column+=1
                    column=7
                    row+=1
                    wb.save("/Users/soulist/Projects/dataset.xlsx")
#   Looking for the second auction information (Ищем информацию о втором аукционе) 
                    try:
                        print ("Следующий аукцион")
                        for elm in header.find_next_sibling("div").find_next_sibling("div").find_all("div"):
                            print(elm.get_text())
                            ws.cell(row=row,column=column).value=elm.get_text()
                            column+=1
#       If second auction is present, writing down all previous metadata on the new row (
#  Если информация о втором аукционе есть, записываем все метаданные по новой на вторую строчку вместе с данными второго аукциона
                        if i.h3.text=="Перейти к работе":
                            print ("Безымянная")
                            ws["B"+str(row)]="Безымянная"
                        else:
                            print (i.h3.text)
                            ws["B"+str(row)]=i.h3.text
                        for v in values:
    #                     print(v.getText())
    #                     print("".join(re.findall(r"^\d{4}$",v.get_text())))
                            year="".join(re.findall(r"^\d{4}",v.get_text()))
                            if len(year)>0:
                                print (year)
                                ws["C"+str(row)]="".join(year)
                        if len(size)!=0:
                            sizestr="".join(size)
                            sizestr.replace("Размер, ","")
                            ws["D"+str(row)]="".join(size)
                        if len(technique)!=0:
                            ws["E"+str(row)]="".join(technique)
    #                     Risk Labeling
                        label=[]
                        labelyellow=i.find("span",{"class":"yellow round"})
                        labelgreen=i.find("span",{"class":"green round"})
                        labelred=i.find("span",{"class":"red round"})

                        if labelyellow is not None:
                            label=[]
                            label.append(labelyellow["class"])
                        if labelgreen is not None:
                            label=[]
                            label.append(labelgreen["class"])
                        if labelred is not None: 
                            label=[]
                            label.append(labelred["class"])
            #             label1=0
            #             label1=list(filter(None, label))
                        try:
                            ws["K"+str(row)]=("".join(label[0]))
                        except IndexError:
                            ws["K"+str(row)]="No Label"

                        try:
                            imageurl=linktoimage["src"].replace("small","big")    
                            request.urlretrieve(imageurl,imagepath)
                            ws["L"+str(row)]=imageurl
                        except KeyboardInterrupt:
                            raise
                        except:
                            continue
#       Numbering all ids one number up (Прибавляем ко всем номерам 1)
                        ws["B"+str(row)]=artistname
                        auctionid+=1
                        paintingartisauctiontid=str(artistid)+str(paintingid)+str(auctionid)
                        ws["A"+str(row)]=paintingartisauctiontid
                        row+=1
#                     Saving the Excel file (Сохраняем в эксель)
                        wb.save("/Users/soulist/Projects/dataset.xlsx")
                    except AttributeError:
                        continue

                    
#           If no more paintings on the page, go to the next page 
# Если больше картин на странице нет, идём на следующую 
            page+=1
            print(page)
            r=requests.get(link+"?page="+str(page))
            soup=bs(r.text)
            print(link+"?page="+str(page))

            print(link)
        wb.save("/Users/soulist/Projects/dataset.xlsx")
        return
print(search())
row=1
# paintings("https://artinvestment.ru/auctions/2126/works.html",1,"Авилов")

1
Alexandra Gav https://artinvestment.ru/auctions/274660


/Users/soulist/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:27: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


https://artinvestment.ru/auctions/274660/works.html
1
Олененок
Следующая картина
Размер - Размер, см*29,5х39,5
Техника - Бумага; акварель
111
2018
23.03.2019
ЛитфондМосква (RU)
204
1 - 1 RUR
9 000 RUR
Следующий аукцион
2
Безымянная
Следующая картина
Размер - Размер, см*31,5х56,5
Техника - Бумага; акварель
121
2018
Следующий аукцион
2
https://artinvestment.ru/auctions/274660/works.html?page=2
https://artinvestment.ru/auctions/274660/works.html
None
2
Gla+Z https://artinvestment.ru/auctions/274680
https://artinvestment.ru/auctions/274680/works.html
1
Огни Москвы
Следующая картина
Размер - Размер, см*29,5х21
Техника - Бумага; акварель
211
23.03.2019
ЛитфондМосква (RU)
206
1 - 1 RUR
1 500 RUR
Следующий аукцион
2
Безымянная
Следующая картина
Размер - Размер, см*42х29,5
Техника - Бумага; акварель
221
Следующий аукцион
2
https://artinvestment.ru/auctions/274680/works.html?page=2
https://artinvestment.ru/auctions/274680/works.html
None
3
Judge Doom https://artinvestment.ru/auctions/274740
http

Следующий аукцион
33
Безымянная
Следующая картина
Размер - Размер, см*12х30
Техника - Холст; масло
10331
2001
Следующий аукцион
34
Безымянная
Следующая картина
Размер - Размер, см*90х120
Техника - Холст; масло
10341
1998
Следующий аукцион
35
Безымянная
Следующая картина
Размер - Размер, см*60х50
Техника - Оргалит; темпера
10351
2006
Следующий аукцион
36
Безымянная
Следующая картина
Размер - Размер, см*50х150
Техника - Холст; масло
10361
1997
Следующий аукцион
37
Безымянная
Следующая картина
Размер - Размер, см*44х67
Техника - Картон; темпера
10371
1998
Следующий аукцион
38
Безымянная
Следующая картина
Размер - Размер, см*80х90
Техника - Холст; темпера
10381
2004
Следующий аукцион
39
Безымянная
Следующая картина
Размер - Размер, см*55х60
Техника - Оргалит; темпера
10391
2006
Следующий аукцион
40
Безымянная
Следующая картина
Размер - Размер, см*55х60
Техника - Оргалит; темпера
10401
2006
Следующий аукцион
41
Безымянная
Следующая картина
Размер - Размер, см*48х86
Техника - Оргалит; масло,

https://artinvestment.ru/auctions/47840/works.html?page=2
https://artinvestment.ru/auctions/47840/works.html
None
17
Абердам, Альфред https://artinvestment.ru/auctions/138540
https://artinvestment.ru/auctions/138540/works.html
1
Zwei sitzende Frauen
Следующая картина
Размер - Размер, см*27х22,2
Техника - Холст; масло
1711
20.09.2019
Schuler AuktionenZurich (CH)
3124
1 000 - 1 500 CHF
1 300 CHF
Следующий аукцион
2
Безымянная
Следующая картина
Размер - Размер, см*73х60
Техника - Холст; масло
1721
1936
Следующий аукцион
3
Безымянная
Следующая картина
Размер - Размер, см*35х27
Техника - Холст; масло
1731
Следующий аукцион
4
Безымянная
Следующая картина
Размер - Размер, см*47х62
Техника - Холст; масло
1741
1962
Следующий аукцион
5
Безымянная
Следующая картина
Размер - Размер, см*47х55
Техника - Холст; масло
1751
Следующий аукцион
6
Безымянная
Следующая картина
Размер - Размер, см*41х27
Техника - Холст; масло
1761
1954
Следующий аукцион
7
Безымянная
Следующая картина
Размер - Размер, см*50х7

...

Следующий аукцион
18
Безымянная
Следующая картина
Размер - Размер, см*82х62,5
Техника - Бумага на холсте; карандаш, акварель, темпера
1397181
Следующий аукцион
19
Безымянная
Следующая картина
Размер - Размер, см*50х70
Техника - Холст; масло
1397191
Следующий аукцион
20
Безымянная
Следующая картина
Размер - Размер, см*24,5х34,5
Техника - Холст на картоне; масло
1397201
1954
Следующий аукцион
21
Безымянная
Следующая картина
Размер - Размер, см*40х30,3
Техника - Бумага на картоне; тушь
1397211
1930
Следующий аукцион
22
Безымянная
Следующая картина
Размер - Размер, см*14х24,5
Техника - Холст; масло
1397221
1934
Следующий аукцион
23
Безымянная
Следующая картина
Размер - Размер, см*64х46
Техника - Бумага; акварель
1397231
1935
Следующий аукцион
24
Безымянная
Следующая картина
Размер - Размер, см*64х46
Техника - Бумага; акварель
1397241
1935
Следующий аукцион
25
Безымянная
Следующая картина
Размер - Размер, см*64х46
Техника - Бумага; акварель
1397251
1935
Следующий аукцион
26
Безымянная
Следу

Следующий аукцион
85
Безымянная
Следующая картина
Размер - Размер, см*58х75
Техника - Холст; масло
1397851
1932
Следующий аукцион
86
Безымянная
Следующая картина
Размер - Размер, см*54х62
Техника - Холст; масло
1397861
Следующий аукцион
87
Безымянная
Следующая картина
Размер - Размер, см*27х34,5
Техника - Холст на картоне; масло
1397871
1948
Следующий аукцион
88
Безымянная
Следующая картина
Размер - Размер, см*60х80
Техника - Холст; масло
1397881
89
Безымянная
Следующая картина
Размер - Размер, см*25х60
Техника - Холст на картоне; масло
1397891
1938
Следующий аукцион
90
Безымянная
Следующая картина
Размер - Размер, см*31х36,5
Техника - Холст на картоне; масло
1397901
1929
Следующий аукцион
4
https://artinvestment.ru/auctions/13950/works.html?page=4
https://artinvestment.ru/auctions/13950/works.html
91
Безымянная
Следующая картина
Размер - Размер, см*71х52
Техника - Бумага; акварель, гуашь
1397911
1934
Следующий аукцион
92
Безымянная
Следующая картина
Размер - Размер, см*46х66
Техника -

Следующий аукцион
5
Безымянная
Следующая картина
Размер - Размер, см*45х71
Техника - Холст; масло
140651
Следующий аукцион
6
Безымянная
Следующая картина
Размер - Размер, см*76х52,5
Техника - Холст; масло
140661
1913
Следующий аукцион
7
Безымянная
Следующая картина
Размер - Размер, см*141х76
Техника - Холст на доске; масло
140671
1907
Следующий аукцион
8
Безымянная
Следующая картина
Размер - Размер, см*51х35
Техника - Картон; пастель
140681
Следующий аукцион
9
Безымянная
Следующая картина
Размер - Размер, см*58,5х46,5
Техника - Холст; масло
140691
Следующий аукцион
10
Безымянная
Следующая картина
Размер - Размер, см*38,5х52
Техника - Холст на картоне; масло
1406101
1880
Следующий аукцион
11
Безымянная
Следующая картина
Размер - Размер, см*127х86
Техника - Холст; масло
1406111
1895
Следующий аукцион
12
Безымянная
Следующая картина
Размер - Размер, см*59х37,5
Техника - Холст; масло
1406121
1916
Следующий аукцион
13
Безымянная
Следующая картина
Размер - Размер, см*26,7х33,6
Техника - Доск

Следующий аукцион
19
Безымянная
Следующая картина
Размер - Размер, см*44,5х54,5
Техника - Холст; масло
1413191
1980
Следующий аукцион
20
Безымянная
Следующая картина
Размер - Размер, см*62х47
Техника - Оргалит; масло
1413201
Следующий аукцион
21
Безымянная
Следующая картина
Размер - Размер, см*46х57,5
Техника - Оргалит; масло
1413211
1984
Следующий аукцион
22
Безымянная
Следующая картина
Размер - Размер, см*18х26,7
Техника - Бумага; смешанная техника (9)
1413221
1956
Следующий аукцион
23
Безымянная
Следующая картина
Размер - Размер, см*23х31,5
Техника - Бумага; смешанная техника
1413231
1966
Следующий аукцион
24
Безымянная
Следующая картина
Размер - Размер, см*25,5х31
Техника - Бумага; смешанная техника
1413241
1966
Следующий аукцион
25
Безымянная
Следующая картина
Размер - Размер, см*50х39
Техника - Холст; масло
1413251
Следующий аукцион
26
Безымянная
Следующая картина
Размер - Размер, см*39х40
Техника - Холст; масло
1413261
1995
Следующий аукцион
27
Безымянная
Следующая картина
Разме

KeyboardInterrupt: 